In [ ]:
import itertools
from scipy.spatial.distance import pdist, cdist
import numpy as np
import pandas as pd

In [ ]:
pos_item = [0,1]

# $IFD_{\div}$

In [ ]:
def get_max_min_IFD_div(num_rel_item, repeat=10, cut_off=False, pos_item=[0,1], dataframe=False):
    min_IFD_div = 99999
    max_IFD_div = -1



    df = pd.DataFrame()

    all_possible_positions_at_repeat = itertools.product(pos_item, repeat=repeat)
    for ori_ranks in all_possible_positions_at_repeat:
        pos_index = np.arange(repeat)+1
        dcg_weight =  1/ np.log2(pos_index+1)
        if cut_off:
            print("Setting",cut_off)
            dcg_weight[cut_off:] = 0

        ranks = np.asarray(ori_ranks)
        count_non_zero = np.count_nonzero(ranks)
        
        if count_non_zero!= num_rel_item:
            continue

        mask = np.where(ranks!=0)
        dcg_weight = dcg_weight[mask]
        ranks = ranks[ranks!=0]
        to_input_to_pairwise = (dcg_weight/ranks).reshape(-1,1)

        IFD_div = cdist(to_input_to_pairwise, to_input_to_pairwise, lambda u, v: max(0,u-v)).mean()

        if dataframe:
            new = {"IFD_score":[IFD_div], "ranks":[ori_ranks]}
            new = pd.DataFrame(new)
            df = pd.concat([df,new], ignore_index=True)

        if IFD_div < min_IFD_div:
            min_IFD_div = IFD_div
            rank_min_IFD_div = ori_ranks
        if IFD_div > max_IFD_div:
            max_IFD_div = IFD_div
            rank_max_IFD_div = ori_ranks


    print(min_IFD_div, rank_min_IFD_div)
    print(max_IFD_div, rank_max_IFD_div)

    if dataframe:
        return df.query("IFD_score==@min_IFD_div | IFD_score==@max_IFD_div")

In [ ]:
def test(num_rel_item, cut_off=False, pos_item=[0,1], dataframe=False):
    list_df = []
    for rel_item in range(1, num_rel_item+1):
        print(rel_item)
        df = get_max_min_IFD_div(rel_item, num_rel_item, cut_off, pos_item, dataframe)
        display(df)
        list_df.append(df)

In [ ]:
# will not work for graded relevance!
def compute_IFD_div(num_rel_item, repeat=10, cut_off=False, fixed=False):
    pos_index = np.arange(repeat)+1
    dcg_weight =  1/ np.log2(pos_index+1)
    if cut_off:
        print("Setting",cut_off)
        dcg_weight[cut_off:] = 0
    print(dcg_weight)

    all_possible_positions_at_repeat = itertools.product(pos_item, repeat=repeat)

    for ranks in all_possible_positions_at_repeat:
        if sum(ranks) != num_rel_item:
            continue
        to_input_to_pairwise = (ranks * dcg_weight )
        if fixed:
            mask = np.where(ranks)
            to_input_to_pairwise = to_input_to_pairwise[mask]
        to_input_to_pairwise = to_input_to_pairwise.reshape(-1,1)
        IFD_div = cdist(to_input_to_pairwise, to_input_to_pairwise, lambda u, v: max(0,u-v)).mean()
        print(ranks, to_input_to_pairwise.reshape(1,-1), IFD_div)

## Limitation 2 (non-localisation)

In [ ]:
compute_IFD_div(2, 5, cut_off=False, fixed=True)
compute_IFD_div(5, 5, cut_off=False, fixed=True)

[1.         0.63092975 0.5        0.43067656 0.38685281]
(0, 0, 0, 1, 1) [[0.43067656 0.38685281]] 0.010955937709712857
(0, 0, 1, 0, 1) [[0.5        0.38685281]] 0.028286798191364593
(0, 0, 1, 1, 0) [[0.5        0.43067656]] 0.017330860481651736
(0, 1, 0, 0, 1) [[0.63092975 0.38685281]] 0.061019236584228975
(0, 1, 0, 1, 0) [[0.63092975 0.43067656]] 0.05006329887451612
(0, 1, 1, 0, 0) [[0.63092975 0.5       ]] 0.03273243839286438
(1, 0, 0, 0, 1) [[1.         0.38685281]] 0.1532867981913646
(1, 0, 0, 1, 0) [[1.         0.43067656]] 0.14233086048165172
(1, 0, 1, 0, 0) [[1.  0.5]] 0.125
(1, 1, 0, 0, 0) [[1.         0.63092975]] 0.09226756160713562
[1.         0.63092975 0.5        0.43067656 0.38685281]
(1, 1, 1, 1, 1) [[1.         0.63092975 0.5        0.43067656 0.38685281]] 0.1141238064823185


In [ ]:
compute_IFD_div(4, 5, cut_off=False, fixed=True)

[1.         0.63092975 0.5        0.43067656 0.38685281]
(0, 1, 1, 1, 1) [[0.63092975 0.5        0.43067656 0.38685281]] 0.05009714255858466
(1, 0, 1, 1, 1) [[1.         0.5        0.43067656 0.38685281]] 0.11929781376393638
(1, 1, 0, 1, 1) [[1.         0.63092975 0.43067656 0.38685281]] 0.12748092336215247
(1, 1, 1, 0, 1) [[1.         0.63092975 0.5        0.38685281]] 0.12314820824173954
(1, 1, 1, 1, 0) [[1.         0.63092975 0.5        0.43067656]] 0.11493125495945489


In [ ]:
compute_IFD_div(3, 5, cut_off=False, fixed=True)

[1.         0.63092975 0.5        0.43067656 0.38685281]
(0, 0, 1, 1, 1) [[0.5        0.43067656 0.38685281]] 0.025143820614546303
(0, 1, 0, 1, 1) [[0.63092975 0.43067656 0.38685281]] 0.054239321408203534
(0, 1, 1, 0, 1) [[0.63092975 0.5        0.38685281]] 0.054239321408203534
(0, 1, 1, 1, 0) [[0.63092975 0.5        0.43067656]] 0.04450071011068099
(1, 0, 0, 1, 1) [[1.         0.43067656 0.38685281]] 0.13625493172565742
(1, 0, 1, 0, 1) [[1.         0.5        0.38685281]] 0.13625493172565742
(1, 0, 1, 1, 0) [[1.         0.5        0.43067656]] 0.12651632042813488
(1, 1, 0, 0, 1) [[1.         0.63092975 0.38685281]] 0.13625493172565742
(1, 1, 0, 1, 0) [[1.         0.63092975 0.43067656]] 0.12651632042813488
(1, 1, 1, 0, 0) [[1.         0.63092975 0.5       ]] 0.1111111111111111


In [ ]:
compute_IFD_div(1, 3, cut_off=False)

[1.         0.63092975 0.5       ]
(0, 0, 1) [[0.  0.  0.5]] 0.1111111111111111
(0, 1, 0) [[0.         0.63092975 0.        ]] 0.14020661190476835
(1, 0, 0) [[1. 0. 0.]] 0.2222222222222222


In [ ]:
compute_IFD_div(1, 3, cut_off=False, fixed=True)

[1.         0.63092975 0.5       ]
(0, 0, 1) [[0.5]] 0.0
(0, 1, 0) [[0.63092975]] 0.0
(1, 0, 0) [[1.]] 0.0


In [ ]:
compute_IFD_div(2, 3, cut_off=False)

[1.         0.63092975 0.5       ]
(0, 1, 1) [[0.         0.63092975 0.5       ]] 0.14020661190476835
(1, 0, 1) [[1.  0.  0.5]] 0.2222222222222222
(1, 1, 0) [[1.         0.63092975 0.        ]] 0.2222222222222222


In [ ]:
compute_IFD_div(2, 3, cut_off=1)

Setting 1
[1. 0. 0.]
(0, 1, 1) [[0. 0. 0.]] 0.0
(1, 0, 1) [[1. 0. 0.]] 0.2222222222222222
(1, 1, 0) [[1. 0. 0.]] 0.2222222222222222


In [ ]:
compute_IFD_div(2, 3, cut_off=2)

Setting 2
[1.         0.63092975 0.        ]
(0, 1, 1) [[0.         0.63092975 0.        ]] 0.14020661190476835
(1, 0, 1) [[1. 0. 0.]] 0.2222222222222222
(1, 1, 0) [[1.         0.63092975 0.        ]] 0.2222222222222222


## Limitation of top-k-insensitivity

The following three cells are the example for the limitation of top k insensitivity explanation (3-Dec)

In [ ]:
compute_IFD_div(2, 3, cut_off=False, fixed=True)

[1.         0.63092975 0.5       ]
(0, 1, 1) [[0.63092975 0.5       ]] 0.03273243839286438
(1, 0, 1) [[1.  0.5]] 0.125
(1, 1, 0) [[1.         0.63092975]] 0.09226756160713562


In [ ]:
compute_IFD_div(2, 3, cut_off=2, fixed=True)

Setting 2
[1.         0.63092975 0.        ]
(0, 1, 1) [[0.63092975 0.        ]] 0.15773243839286438
(1, 0, 1) [[1. 0.]] 0.25
(1, 1, 0) [[1.         0.63092975]] 0.09226756160713562


In [ ]:
# just for comparison
compute_IFD_div(2, 3, cut_off=1, fixed=True)

Setting 1
[1. 0. 0.]
(0, 1, 1) [[0. 0.]] 0.0
(1, 0, 1) [[1. 0.]] 0.25
(1, 1, 0) [[1. 0.]] 0.25


## No cut-off setting (all items are seen as exposed)

In [ ]:
pos_item = [0,1]
test(10)

1
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
2
0.0029912923365233296 (0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
0.17773379342052803 (1, 0, 0, 0, 0, 0, 0, 0, 0, 1)
3
0.005866677881742419 (0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
0.15798559415158048 (1, 0, 0, 0, 0, 0, 0, 0, 1, 1)
4
0.009202525135505242 (0, 0, 0, 0, 0, 0, 1, 1, 1, 1)
0.1539190799346133 (1, 1, 0, 0, 0, 0, 0, 0, 1, 1)
5
0.013327044739969658 (0, 0, 0, 0, 0, 1, 1, 1, 1, 1)
0.14014160842173606 (1, 1, 0, 0, 0, 0, 0, 1, 1, 1)
6
0.01867610931841656 (0, 0, 0, 0, 1, 1, 1, 1, 1, 1)
0.13135861848186836 (1, 1, 1, 0, 0, 0, 0, 1, 1, 1)
7
0.026009107295099174 (0, 0, 0, 1, 1, 1, 1, 1, 1, 1)
0.12151592490104328 (1, 1, 1, 0, 0, 0, 1, 1, 1, 1)
8
0.03690338551473393 (0, 0, 1, 1, 1, 1, 1, 1, 1, 1)
0.113703024995235 (1, 1, 1, 1, 0, 0, 1, 1, 1, 1)
9
0.05551389033330548 (0, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.10616922073134516 (1, 1, 1, 1, 0, 1, 1, 1, 1, 1)
10
0.09953065778909398 (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.09953065778909398 (1, 1, 1, 1, 1, 1, 

In [ ]:
# try with odd number of items
test(15)

1
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
2
0.0014895062024538747 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
0.1875 (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
3
0.0028110077860430157 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
0.16666666666666666 (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
4
0.004212873344333581 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1)
0.16406073304760263 (1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
5
0.005773281673581119 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1)
0.14999773830093135 (1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
6
0.007551875375097463 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1)
0.1420073792013259 (1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
7
0.009616204107021414 (0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1)
0.13213444581575878 (1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1)
8
0.012055697763075357 (0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1)
0.12495856941160473 (1, 1, 1, 1

## non-binary relevance

In [ ]:
pos_item = [0,0.5,1]
test(10, pos_item=pos_item)

1
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0.5)
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0.5)
2
0.0 (0, 1, 0, 0, 0, 0, 0, 0.5, 0, 0)
0.42773379342052803 (0.5, 0, 0, 0, 0, 0, 0, 0, 0, 1)
3
0.005866677881742419 (0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
0.38020781637380274 (0.5, 0, 0, 0, 0.5, 0, 0, 0, 0, 1)
4
0.009202525135505242 (0, 0, 0, 0, 0, 0, 1, 1, 1, 1)
0.3808521895328294 (0.5, 0.5, 0, 0, 0, 0, 0, 0, 1, 1)
5
0.013327044739969658 (0, 0, 0, 0, 0, 1, 1, 1, 1, 1)
0.35061598870745264 (0.5, 0.5, 0, 0, 0, 0, 0, 0.5, 1, 1)
6
0.01867610931841656 (0, 0, 0, 0, 1, 1, 1, 1, 1, 1)
0.33671387572393424 (0.5, 0.5, 0.5, 0, 0, 0, 0, 1, 1, 1)
7
0.026009107295099174 (0, 0, 0, 1, 1, 1, 1, 1, 1, 1)
0.3158775374374888 (0.5, 0.5, 0.5, 0, 0, 0, 1, 1, 1, 1)
8
0.03690338551473393 (0, 0, 1, 1, 1, 1, 1, 1, 1, 1)
0.3025362332129019 (0.5, 0.5, 0.5, 0.5, 0, 0, 1, 1, 1, 1)
9
0.05469884292681903 (0, 1, 1, 1, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5)
0.28699553724462334 (0.5, 0.5, 0.5, 0.5, 0, 0.5, 1, 1, 1, 1)
10
0.07620983135311647 (1, 1, 1, 0.5, 0.5, 0.5,

## Try with fixed examination (cut-off at k)

In [ ]:
pos_item = [0,1]
compute_IFD_div(5,8, cut_off=8, fixed=True)

Setting 8
[1.         0.63092975 0.5        0.43067656 0.38685281 0.35620719
 0.33333333 0.31546488]
(0, 0, 0, 1, 1, 1, 1, 1) [[0.43067656 0.38685281 0.35620719 0.33333333 0.31546488]] 0.022715426918122953
(0, 0, 1, 0, 1, 1, 1, 1) [[0.5        0.38685281 0.35620719 0.33333333 0.31546488]] 0.03380717762638006
(0, 0, 1, 1, 0, 1, 1, 1) [[0.5        0.43067656 0.35620719 0.33333333 0.31546488]] 0.03731307769348818
(0, 0, 1, 1, 1, 0, 1, 1) [[0.5        0.43067656 0.38685281 0.33333333 0.31546488]] 0.03731307769348818
(0, 0, 1, 1, 1, 1, 0, 1) [[0.5        0.43067656 0.38685281 0.35620719 0.31546488]] 0.03548316939151307
(0, 0, 1, 1, 1, 1, 1, 0) [[0.5        0.43067656 0.38685281 0.35620719 0.33333333]] 0.03262421634389634
(0, 1, 0, 0, 1, 1, 1, 1) [[0.63092975 0.38685281 0.35620719 0.33333333 0.31546488]] 0.05475593819781326
(0, 1, 0, 1, 0, 1, 1, 1) [[0.63092975 0.43067656 0.35620719 0.33333333 0.31546488]] 0.05826183826492138
(0, 1, 0, 1, 1, 0, 1, 1) [[0.63092975 0.43067656 0.38685281 0.3333

In [ ]:
compute_IFD_div(5,50, cut_off=10, fixed=True)

Streaming output truncated to the last 5000 lines.
(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1) [[0. 0. 0. 0. 0.]] 0.0
(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0) [[0. 0. 0. 0. 0.]] 0.0
(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0) [[0. 0. 0. 0. 0.]] 0.0
(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0) [[0. 0. 0. 0. 0.]] 0.0
(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0) [[0. 0. 0. 0. 0.]] 0.0
(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 

In [ ]:
pos_item = [0,1]
test(10,cut_off=5, pos_item=pos_item)
test(15,cut_off=5, pos_item=pos_item)

1
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
2
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
0.25 (1, 0, 0, 0, 0, 0, 0, 0, 0, 1)
3
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
0.2222222222222222 (1, 0, 0, 0, 0, 0, 0, 0, 1, 1)
4
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 1, 1, 1, 1)
0.22693310959821608 (1, 1, 0, 0, 0, 0, 0, 0, 1, 1)
5
Setting 5
0.0 (0, 0, 0, 0, 0, 1, 1, 1, 1, 1)
0.21047438028571663 (1, 1, 0, 0, 0, 0, 0, 1, 1, 1)
6
Setting 5
0.053729556560353005 (0, 0, 0, 0, 1, 1, 1, 1, 1, 1)
0.20535525724206594 (1, 1, 1, 0, 0, 0, 0, 1, 1, 1)
7
Setting 5
0.08431572606894948 (0, 0, 0, 1, 1, 1, 1, 1, 1, 1)
0.19436161253644554 (1, 1, 1, 0, 0, 0, 1, 1, 1, 1)
8
Setting 5
0.10646783143860297 (0, 0, 1, 1, 1, 1, 1, 1, 1, 1)
0.1888332082176669 (1, 1, 1, 1, 0, 0, 1, 1, 1, 1)
9
Setting 5
0.13017098611523847 (0, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.18082631651327818 (1, 1, 1, 1, 1, 0, 1, 1, 1, 1)
10
Setting 5
0.1759539075645492 (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.1759539075645492 (1, 

In [ ]:
pos_item = [0,0.5,1]
test(10,cut_off=5, pos_item=pos_item)

1
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0.5)
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0.5)
2
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0.5, 0.5)
0.5 (0.5, 0, 0, 0, 0, 0, 0, 0, 0, 0.5)
3
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 0.5, 0.5, 0.5)
0.4444444444444444 (0.5, 0, 0, 0, 0, 0, 0, 0, 0.5, 0.5)
4
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0.5, 0.5, 0.5, 0.5)
0.45386621919643216 (0.5, 0.5, 0, 0, 0, 0, 0, 0, 0.5, 0.5)
5
Setting 5
0.0 (0, 0, 0, 0, 0, 0.5, 0.5, 0.5, 0.5, 0.5)
0.42094876057143327 (0.5, 0.5, 0, 0, 0, 0, 0, 0.5, 0.5, 0.5)
6
Setting 5
0.053729556560353005 (0, 0, 0, 0, 1, 0.5, 0.5, 0.5, 0.5, 0.5)
0.41071051448413187 (0.5, 0.5, 0.5, 0, 0, 0, 0, 0.5, 0.5, 0.5)
7
Setting 5
0.08431572606894948 (0, 0, 0, 1, 1, 0.5, 0.5, 0.5, 0.5, 0.5)
0.3887232250728911 (0.5, 0.5, 0.5, 0, 0, 0, 0.5, 0.5, 0.5, 0.5)
8
Setting 5
0.10646783143860297 (0, 0, 1, 1, 1, 0.5, 0.5, 0.5, 0.5, 0.5)
0.3776664164353338 (0.5, 0.5, 0.5, 0.5, 0, 0, 0.5, 0.5, 0.5, 0.5)
9
Setting 5
0.13017098611523847 (0, 1, 1, 1, 1, 0.5, 0.5, 0.5, 0.5, 0.

## Resolving non-realisability

### Examples

In [ ]:
#example of resolving IFD div, non-realisability
pos_item = [0,1]
test(10,cut_off=5, pos_item=pos_item, dataframe=True)

1
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)


IFD_score                           ranks
0        0.0  (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
1        0.0  (0, 0, 0, 0, 0, 0, 0, 0, 1, 0)
2        0.0  (0, 0, 0, 0, 0, 0, 0, 1, 0, 0)
3        0.0  (0, 0, 0, 0, 0, 0, 1, 0, 0, 0)
4        0.0  (0, 0, 0, 0, 0, 1, 0, 0, 0, 0)
5        0.0  (0, 0, 0, 0, 1, 0, 0, 0, 0, 0)
6        0.0  (0, 0, 0, 1, 0, 0, 0, 0, 0, 0)
7        0.0  (0, 0, 1, 0, 0, 0, 0, 0, 0, 0)
8        0.0  (0, 1, 0, 0, 0, 0, 0, 0, 0, 0)
9        0.0  (1, 0, 0, 0, 0, 0, 0, 0, 0, 0)

2
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
0.25 (1, 0, 0, 0, 0, 0, 0, 0, 0, 1)


IFD_score                           ranks
0        0.00  (0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
1        0.00  (0, 0, 0, 0, 0, 0, 0, 1, 0, 1)
2        0.00  (0, 0, 0, 0, 0, 0, 0, 1, 1, 0)
3        0.00  (0, 0, 0, 0, 0, 0, 1, 0, 0, 1)
4        0.00  (0, 0, 0, 0, 0, 0, 1, 0, 1, 0)
5        0.00  (0, 0, 0, 0, 0, 0, 1, 1, 0, 0)
6        0.00  (0, 0, 0, 0, 0, 1, 0, 0, 0, 1)
7        0.00  (0, 0, 0, 0, 0, 1, 0, 0, 1, 0)
8        0.00  (0, 0, 0, 0, 0, 1, 0, 1, 0, 0)
9        0.00  (0, 0, 0, 0, 0, 1, 1, 0, 0, 0)
36       0.25  (1, 0, 0, 0, 0, 0, 0, 0, 0, 1)
37       0.25  (1, 0, 0, 0, 0, 0, 0, 0, 1, 0)
38       0.25  (1, 0, 0, 0, 0, 0, 0, 1, 0, 0)
39       0.25  (1, 0, 0, 0, 0, 0, 1, 0, 0, 0)
40       0.25  (1, 0, 0, 0, 0, 1, 0, 0, 0, 0)

3
Setting 5
0.0 (0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
0.2222222222222222 (1, 0, 0, 0, 0, 0, 0, 0, 1, 1)


...

IFD_score                           ranks
0    0.106468  (0, 0, 1, 1, 1, 1, 1, 1, 1, 1)
30   0.188833  (1, 1, 1, 1, 0, 0, 1, 1, 1, 1)
31   0.188833  (1, 1, 1, 1, 0, 1, 0, 1, 1, 1)
32   0.188833  (1, 1, 1, 1, 0, 1, 1, 0, 1, 1)
33   0.188833  (1, 1, 1, 1, 0, 1, 1, 1, 0, 1)
34   0.188833  (1, 1, 1, 1, 0, 1, 1, 1, 1, 0)

9
Setting 5
0.13017098611523847 (0, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.18082631651327818 (1, 1, 1, 1, 1, 0, 1, 1, 1, 1)


IFD_score                           ranks
0   0.130171  (0, 1, 1, 1, 1, 1, 1, 1, 1, 1)
5   0.180826  (1, 1, 1, 1, 1, 0, 1, 1, 1, 1)
6   0.180826  (1, 1, 1, 1, 1, 1, 0, 1, 1, 1)
7   0.180826  (1, 1, 1, 1, 1, 1, 1, 0, 1, 1)
8   0.180826  (1, 1, 1, 1, 1, 1, 1, 1, 0, 1)
9   0.180826  (1, 1, 1, 1, 1, 1, 1, 1, 1, 0)

10
Setting 5
0.1759539075645492 (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.1759539075645492 (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)


IFD_score                           ranks
0   0.175954  (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)

In [ ]:
#also example for resolving non-realisability
test(10,cut_off=7, pos_item=pos_item, dataframe=True)

1
Setting 7
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)


IFD_score                           ranks
0        0.0  (0, 0, 0, 0, 0, 0, 0, 0, 0, 1)
1        0.0  (0, 0, 0, 0, 0, 0, 0, 0, 1, 0)
2        0.0  (0, 0, 0, 0, 0, 0, 0, 1, 0, 0)
3        0.0  (0, 0, 0, 0, 0, 0, 1, 0, 0, 0)
4        0.0  (0, 0, 0, 0, 0, 1, 0, 0, 0, 0)
5        0.0  (0, 0, 0, 0, 1, 0, 0, 0, 0, 0)
6        0.0  (0, 0, 0, 1, 0, 0, 0, 0, 0, 0)
7        0.0  (0, 0, 1, 0, 0, 0, 0, 0, 0, 0)
8        0.0  (0, 1, 0, 0, 0, 0, 0, 0, 0, 0)
9        0.0  (1, 0, 0, 0, 0, 0, 0, 0, 0, 0)

2
Setting 7
0.0 (0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
0.25 (1, 0, 0, 0, 0, 0, 0, 0, 0, 1)


IFD_score                           ranks
0        0.00  (0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
1        0.00  (0, 0, 0, 0, 0, 0, 0, 1, 0, 1)
2        0.00  (0, 0, 0, 0, 0, 0, 0, 1, 1, 0)
36       0.25  (1, 0, 0, 0, 0, 0, 0, 0, 0, 1)
37       0.25  (1, 0, 0, 0, 0, 0, 0, 0, 1, 0)
38       0.25  (1, 0, 0, 0, 0, 0, 0, 1, 0, 0)

3
Setting 7
0.0 (0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
0.2222222222222222 (1, 0, 0, 0, 0, 0, 0, 0, 1, 1)


...

IFD_score                           ranks
0    0.106825  (0, 0, 1, 1, 1, 1, 1, 1, 1, 1)
30   0.183625  (1, 1, 1, 1, 0, 0, 1, 1, 1, 1)

9
Setting 7
0.12194053344034135 (0, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.17259586383838108 (1, 1, 1, 1, 0, 1, 1, 1, 1, 1)


IFD_score                           ranks
0   0.121941  (0, 1, 1, 1, 1, 1, 1, 1, 1, 1)
4   0.172596  (1, 1, 1, 1, 0, 1, 1, 1, 1, 1)

10
Setting 7
0.162391835693469 (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)
0.162391835693469 (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)


IFD_score                           ranks
0   0.162392  (1, 1, 1, 1, 1, 1, 1, 1, 1, 1)

### Simulation

In [ ]:
def get_max_IFD_div(num_rel_item, repeat=10, cut_off=False, pos_item=[0,1], dataframe=False):
    min_IFD_div = 99999
    max_IFD_div = -1

    if cut_off:
        print("Setting",cut_off)

    df = pd.DataFrame()

    all_possible_positions_at_repeat = itertools.product(pos_item, repeat=repeat)
    for ori_ranks in all_possible_positions_at_repeat:
        pos_index = np.arange(repeat)+1
        dcg_weight =  1/ np.log2(pos_index+1)
        if cut_off:
            dcg_weight[cut_off:] = 0

        ranks = np.asarray(ori_ranks)
        count_non_zero = np.count_nonzero(ranks)
        if count_non_zero!= num_rel_item:
            continue
        mask = np.where(ranks!=0)
        dcg_weight = dcg_weight[mask]
        ranks = ranks[ranks!=0]
        to_input_to_pairwise = (dcg_weight/ranks).reshape(-1,1)

        IFD_div = cdist(to_input_to_pairwise, to_input_to_pairwise, lambda u, v: max(0,u-v)).mean()

        if dataframe:
            new = {"IFD_score":[IFD_div], "ranks":[ori_ranks]}
            new = pd.DataFrame(new)
            df = pd.concat([df,new], ignore_index=True)

        if IFD_div > max_IFD_div:
            max_IFD_div = IFD_div
            rank_max_IFD_div = ori_ranks

    print(max_IFD_div, rank_max_IFD_div)

    if dataframe:
        half = num_rel_item//2
        list_to_check_1 = tuple([1]*half+[0]*(repeat-num_rel_item)+[1]*(half+1))
        list_to_check_2 =  tuple([1]*(half+1)+[0]*(repeat-num_rel_item)+[1]*(half))
        df = df.query("ranks==@list_to_check_1 | ranks==@list_to_check_2")
        return df

In [ ]:
def test_max_IFD_div(num_rel_item, cut_off=False, pos_item=[0,1], dataframe=False, count_rare_case=count_rare_case):
    for rel_item in range(3, num_rel_item,2):
        print(rel_item)
        df = get_max_IFD_div(rel_item, num_rel_item, cut_off, pos_item, dataframe)
        display(df)
        if len(df) <2:
            print("Rare case found!")
            count_rare_case+=1
    return count_rare_case

In [ ]:
count_rare_case =0
for num_item in [10,15,20]:
    for k in [1, 3, 5,10]:
        print(f"====Num item: {num_item}, cut-off: {k}===")
        count_rare_case = test_max_IFD_div(num_item,cut_off=k, pos_item=pos_item, dataframe=True, count_rare_case=count_rare_case)

====Num item: 10, cut-off: 1===
3
Setting 1
0.2222222222222222 (1, 0, 0, 0, 0, 0, 0, 0, 1, 1)


IFD_score                           ranks
84    0.222222  (1, 0, 0, 0, 0, 0, 0, 0, 1, 1)
112   0.222222  (1, 1, 0, 0, 0, 0, 0, 0, 0, 1)

5
Setting 1
0.16 (1, 0, 0, 0, 0, 0, 1, 1, 1, 1)


IFD_score                           ranks
196       0.16  (1, 1, 0, 0, 0, 0, 0, 1, 1, 1)
231       0.16  (1, 1, 1, 0, 0, 0, 0, 0, 1, 1)

7
Setting 1
0.12244897959183673 (1, 0, 0, 0, 1, 1, 1, 1, 1, 1)


...

IFD_score                                              ranks
14217   0.153019  (1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 1, 1, 1, ...
14712   0.153019  (1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 1, 1, ...

17
Setting 10
0.14649173286561795 (1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1)


IFD_score                                              ranks
920   0.146492  (1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, ...
975   0.146492  (1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, ...

19
Setting 10
0.14084515186067734 (1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1)


IFD_score                                              ranks
9    0.140845  (1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, ...
10   0.140845  (1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, ...

In [ ]:
count_rare_case

0

In [ ]:
compute_IFD_div(9, 10, cut_off=7, fixed=True)

Setting 7
[1.         0.63092975 0.5        0.43067656 0.38685281 0.35620719
 0.33333333 0.         0.         0.        ]
(0, 1, 1, 1, 1, 1, 1, 1, 1, 1) [[0.63092975 0.5        0.43067656 0.38685281 0.35620719 0.33333333
  0.         0.         0.        ]] 0.12194053344034135
(1, 0, 1, 1, 1, 1, 1, 1, 1, 1) [[1.         0.5        0.43067656 0.38685281 0.35620719 0.33333333
  0.         0.         0.        ]] 0.1583919158036542
(1, 1, 0, 1, 1, 1, 1, 1, 1, 1) [[1.         0.63092975 0.43067656 0.38685281 0.35620719 0.33333333
  0.         0.         0.        ]] 0.1680904160682066
(1, 1, 1, 0, 1, 1, 1, 1, 1, 1) [[1.         0.63092975 0.5        0.38685281 0.35620719 0.33333333
  0.         0.         0.        ]] 0.1715137959164341
(1, 1, 1, 1, 0, 1, 1, 1, 1, 1) [[1.         0.63092975 0.5        0.43067656 0.35620719 0.33333333
  0.         0.         0.        ]] 0.17259586383838108
(1, 1, 1, 1, 1, 0, 1, 1, 1, 1) [[1.         0.63092975 0.5        0.43067656 0.38685281 0.33333333
 

In [ ]:
compute_IFD_div(15, 20, cut_off=10, fixed=True)

Streaming output truncated to the last 5000 lines.
  0.31546488 0.28906483 0.         0.         0.         0.
  0.         0.         0.        ]] 0.1528597549015797
(1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 0, 1, 1, 1) [[1.         0.63092975 0.5        0.43067656 0.38685281 0.35620719
  0.31546488 0.28906483 0.         0.         0.         0.
  0.         0.         0.        ]] 0.1528597549015797
(1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1) [[1.         0.63092975 0.5        0.43067656 0.38685281 0.35620719
  0.31546488 0.28906483 0.         0.         0.         0.
  0.         0.         0.        ]] 0.1528597549015797
(1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1) [[1.         0.63092975 0.5        0.43067656 0.38685281 0.35620719
  0.31546488 0.28906483 0.         0.         0.         0.
  0.         0.         0.        ]] 0.1528597549015797
(1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 0) [[1.         0.63092975 0.5        0.

# $IFD_\times$

In [ ]:
def get_max_min_IFD_mul(num_rel_item, repeat=10, cut_off=True):
    min_IFD_mul = 99999
    max_IFD_mul = -1

    pos_index = np.arange(repeat)+1
    dcg_weight =  1/ np.log2(pos_index+1)
    if cut_off:
        dcg_weight[cut_off:] = 0

    all_possible_positions_at_repeat = itertools.product(pos_item, repeat=repeat) #position of rel items, otherwise it's 0 anyway

    for ranks in all_possible_positions_at_repeat:
        ranks = np.asarray(ranks)
        count_non_zero = np.count_nonzero(ranks)
        if count_non_zero!= num_rel_item:
            continue

        to_input_to_pairwise = (ranks * dcg_weight ).reshape(-1,1)
        IFD_mul_pdist = pdist(to_input_to_pairwise, 'sqeuclidean')
        # print(IFD_mul_pdist)
        IFD_mul = IFD_mul_pdist.mean()
        if IFD_mul < min_IFD_mul:
            min_IFD_mul = IFD_mul
            rank_min_IFD_mul = ranks

        if IFD_mul > max_IFD_mul:
            max_IFD_mul = IFD_mul
            rank_max_IFD_mul = ranks

    print(min_IFD_mul, rank_min_IFD_mul)
    print(max_IFD_mul, rank_max_IFD_mul)


In [ ]:
def test_IFD_mul(num_rel_item, cut_off=5):
    for rel_item in range(1, num_rel_item+1):
        print(rel_item)
        get_max_min_IFD_mul(rel_item, num_rel_item, cut_off)


## binary relevance

In [ ]:
pos_item = [0,1]
test_IFD_mul(3, cut_off=2)

1
0.0 [0 0 1]
0.6666666666666666 [1 0 0]
2
0.2653815692944934 [0 1 1]
0.6666666666666666 [1 0 1]
3
0.5114284002468551 [1 1 1]
0.5114284002468551 [1 1 1]


In [ ]:
# limitation 1
test_IFD_mul(10, cut_off=10)

1
0.016711694762838136 [0 0 0 0 0 0 0 0 0 1]
0.2 [1 0 0 0 0 0 0 0 0 0]
2
0.030968076046814633 [0 0 0 0 0 0 0 0 1 1]
0.25157314840739436 [1 1 0 0 0 0 0 0 0 0]
3
0.04259817417463911 [0 0 0 0 0 0 0 1 1 1]
0.2653302649946953 [1 1 1 0 0 0 0 0 0 0]
4
0.05140469715585987 [0 0 0 0 0 0 1 1 1 1]
0.2616382137844025 [1 1 1 1 0 0 0 0 0 0]
5
0.05716796020345727 [0 0 0 0 0 1 1 1 1 1]
0.24752636189125024 [1 1 1 1 1 0 0 0 0 0]
6
0.05967369031333229 [0 0 0 0 1 1 1 1 1 1]
0.22635824229389895 [1 1 1 1 1 0 0 0 0 1]
7
0.058833229506262165 [0 0 0 1 1 1 1 1 1 1]
0.20116686198802253 [1 1 1 1 1 0 0 0 1 1]
8
0.05521923873922022 [0 0 1 1 1 1 1 1 1 1]
0.1719959682521481 [1 1 1 1 0 0 1 1 1 1]
9
0.05315972437182705 [0 1 1 1 1 1 1 1 1 1]
0.13729716978671913 [1 1 1 0 1 1 1 1 1 1]
10
0.09566819823456729 [1 1 1 1 1 1 1 1 1 1]
0.09566819823456729 [1 1 1 1 1 1 1 1 1 1]


In [ ]:
test_IFD_mul(15, cut_off=5)

1
0.0 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 1]
0.13333333333333333 [1 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
2
0.0 [0 0 0 0 0 0 0 0 0 0 0 0 0 1 1]
0.1743919376003947 [1 1 0 0 0 0 0 0 0 0 0 0 0 0 0]
3
0.0 [0 0 0 0 0 0 0 0 0 0 0 0 1 1 1]
0.19219260661399987 [1 1 1 0 0 0 0 0 0 0 0 0 0 0 0]
4
0.0 [0 0 0 0 0 0 0 0 0 0 0 1 1 1 1]
0.19944278931787177 [1 1 1 1 0 0 0 0 0 0 0 0 0 0 0]
5
0.0 [0 0 0 0 0 0 0 0 0 0 1 1 1 1 1]
0.20052128586200868 [1 1 1 1 1 0 0 0 0 0 0 0 0 0 0]
6
0.0 [0 0 0 0 0 0 0 0 0 1 1 1 1 1 1]
0.20052128586200868 [1 1 1 1 1 0 0 0 0 0 0 0 0 0 1]
7
0.0 [0 0 0 0 0 0 0 0 1 1 1 1 1 1 1]
0.20052128586200868 [1 1 1 1 1 0 0 0 0 0 0 0 0 1 1]
8
0.0 [0 0 0 0 0 0 0 1 1 1 1 1 1 1 1]
0.20052128586200868 [1 1 1 1 1 0 0 0 0 0 0 0 1 1 1]
9
0.0 [0 0 0 0 0 0 1 1 1 1 1 1 1 1 1]
0.20052128586200868 [1 1 1 1 1 0 0 0 0 0 0 1 1 1 1]
10
0.0 [0 0 0 0 0 1 1 1 1 1 1 1 1 1 1]
0.20052128586200868 [1 1 1 1 1 0 0 0 0 0 1 1 1 1 1]
11
0.01995401259536606 [0 0 0 0 1 1 1 1 1 1 1 1 1 1 1]
0.20052128586200868 [1 1 1 1 1 0 0 0 0 1 1 1 

## graded relevance

In [ ]:
pos_item = [0, 0.5, 1]
test_IFD_mul(10, cut_off=10)

1
0.004177923690709534 [0.  0.  0.  0.  0.  0.  0.  0.  0.  0.5]
0.2 [1 0 0 0 0 0 0 0 0 0]
2
0.007742019011703658 [0.  0.  0.  0.  0.  0.  0.  0.  0.5 0.5]
0.25157314840739436 [1 1 0 0 0 0 0 0 0 0]
3
0.010649543543659778 [0.  0.  0.  0.  0.  0.  0.  0.5 0.5 0.5]
0.2653302649946953 [1 1 1 0 0 0 0 0 0 0]
4
0.012851174288964968 [0.  0.  0.  0.  0.  0.  0.5 0.5 0.5 0.5]
0.2616382137844025 [1 1 1 1 0 0 0 0 0 0]
5
0.014291990050864317 [0.  0.  0.  0.  0.  0.5 0.5 0.5 0.5 0.5]
0.24936124228465822 [1.  1.  1.  1.  0.  0.  0.  0.  0.  0.5]
6
0.014918422578333073 [0.  0.  0.  0.  0.5 0.5 0.5 0.5 0.5 0.5]
0.23578933011926836 [1.  1.  1.  1.  0.  0.  0.  0.  0.5 0.5]
7
0.014708307376565541 [0.  0.  0.  0.5 0.5 0.5 0.5 0.5 0.5 0.5]
0.22073914755174479 [1.  1.  1.  1.  0.  0.  0.  0.5 0.5 0.5]
8
0.013804809684805054 [0.  0.  0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5]
0.20408788800021047 [1.  1.  1.  0.  0.  0.5 0.5 0.5 0.5 0.5]
9
0.013289931092956762 [0.  0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5]
0.186395294812374

## Resolving non-realisability

In [ ]:
def get_max_min_IFD_mul(num_rel_item, repeat=10, cut_off=False, pos_item=[0,1], dataframe=False):
    min_IFD_mul = 99999
    max_IFD_mul = -1

    pos_index = np.arange(repeat)+1
    dcg_weight =  1/ np.log2(pos_index+1)

    if cut_off:
        print("Setting",cut_off)
        dcg_weight[cut_off:] = 0

    df = pd.DataFrame()

    all_possible_positions_at_repeat = itertools.product(pos_item, repeat=repeat)
    for ranks in all_possible_positions_at_repeat:
        ranks = np.asarray(ranks)
        count_non_zero = np.count_nonzero(ranks)
        if count_non_zero!= num_rel_item:
            continue

        to_input_to_pairwise = (ranks * dcg_weight ).reshape(-1,1)
        IFD_mul_pdist = pdist(to_input_to_pairwise, 'sqeuclidean')
        IFD_mul = IFD_mul_pdist.mean()
        if IFD_mul < min_IFD_mul:
            min_IFD_mul = IFD_mul
            rank_min_IFD_mul = ranks

        if IFD_mul > max_IFD_mul:
            max_IFD_mul = IFD_mul
            rank_max_IFD_mul = ranks

        if dataframe:
            new = {"IFD_score":[IFD_mul], "ranks":[tuple(ranks)]}
            new = pd.DataFrame(new)
            df = pd.concat([df,new], ignore_index=True)


    print(min_IFD_mul, rank_min_IFD_mul)
    print(max_IFD_mul, rank_max_IFD_mul)

    if dataframe:
        num_non_rel = repeat - num_rel_item
        list_to_check_min = tuple([0]*num_non_rel + [1]*num_rel_item)
        list_to_check_max = tuple([1]*num_rel_item + [0]*num_non_rel)
        half = num_rel_item//2
        if num_rel_item % 2:
            list_to_max_2 = tuple([1]*half+[0]*(num_non_rel)+[1]*(half+1))
            list_to_max_3 =  tuple([1]*(half+1)+[0]*(num_non_rel)+[1]*(half))
            temp_df = df.query("ranks==@list_to_check_min | ranks==@list_to_check_max | ranks==@list_to_max_2 | ranks==@list_to_max_3")
        else:
            list_to_check_max_2 = tuple([1]*half+[0]*num_non_rel+[1]*half)
            temp_df = df.query("ranks==@list_to_check_min | ranks==@list_to_check_max | ranks==@list_to_check_max_2")

        unique_score = temp_df.IFD_score.unique()
        assert min_IFD_mul in unique_score
        try:
            assert max_IFD_mul in unique_score
        except:
            print("Assertion fails for max IFD mul")
            temp_df = df.query("IFD_score==@max_IFD_mul")
        return temp_df

In [ ]:
def test_max_min_IFD_mul(num_rel_item, cut_off=False, pos_item=[0,1], dataframe=False):
    for rel_item in range(2, num_rel_item,1):
        print("Num of rel items: ", rel_item, "out of", num_rel_item, "items")
        df = get_max_min_IFD_mul(rel_item, num_rel_item, cut_off, pos_item, dataframe)
        display(df)

In [ ]:
#explanation in paper
for num_item in [10,15,20]:
    for k in [1, 3, 5,10]:
        print(f"====Num item: {num_item}, cut-off: {k}===")
        test_max_min_IFD_mul(num_item,cut_off=k, pos_item=pos_item, dataframe=True)

====Num item: 10, cut-off: 1===
Num of rel items:  2 out of 10 items
Setting 1
0.0 [0 0 0 0 0 0 0 0 1 1]
0.2 [1 0 0 0 0 0 0 0 0 1]


IFD_score                           ranks
0         0.0  (0, 0, 0, 0, 0, 0, 0, 0, 1, 1)
36        0.2  (1, 0, 0, 0, 0, 0, 0, 0, 0, 1)
44        0.2  (1, 1, 0, 0, 0, 0, 0, 0, 0, 0)

Num of rel items:  3 out of 10 items
Setting 1
0.0 [0 0 0 0 0 0 0 1 1 1]
0.2 [1 0 0 0 0 0 0 0 1 1]


IFD_score                           ranks
0          0.0  (0, 0, 0, 0, 0, 0, 0, 1, 1, 1)
84         0.2  (1, 0, 0, 0, 0, 0, 0, 0, 1, 1)
112        0.2  (1, 1, 0, 0, 0, 0, 0, 0, 0, 1)
119        0.2  (1, 1, 1, 0, 0, 0, 0, 0, 0, 0)

Num of rel items:  4 out of 10 items
Setting 1
0.0 [0 0 0 0 0 0 1 1 1 1]
0.2 [1 0 0 0 0 0 0 1 1 1]


...

IFD_score                                              ranks
854   0.164153  (1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, ...

Num of rel items:  18 out of 20 items
Setting 10
0.07080601359543601 [0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
0.16202404440202475 [1 1 1 1 1 1 1 1 0 0 1 1 1 1 1 1 1 1 1 1]
Assertion fails for max IFD mul


IFD_score                                              ranks
124   0.162024  (1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, ...

Num of rel items:  19 out of 20 items
Setting 10
0.09126941040009237 [0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
0.1585584617452732 [1 1 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1]


IFD_score                                              ranks
0    0.091269  (0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...
9    0.158558  (1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, ...
10   0.153969  (1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, ...
19   0.153969  (1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...

In [ ]:
def compute_IFD_mul(ranks, cut_off=5):
    num_item = len(ranks)
    pos_index = np.arange(num_item)+1
    dcg_weight =  1/ np.log2(pos_index+1)
    if cut_off:
        dcg_weight[cut_off:] = 0

    ranks = np.asarray(ranks)
    to_input_to_pairwise = (ranks * dcg_weight ).reshape(-1,1)
    IFD_mul_pdist = pdist(to_input_to_pairwise, 'sqeuclidean')
    IFD_mul = IFD_mul_pdist.mean()
    return IFD_mul

In [ ]:
def compute_dcg_weight(num_item, cut_off=5):
    pos_index = np.arange(num_item)+1
    dcg_weight =  1/ np.log2(pos_index+1)
    return dcg_weight

In [ ]:
#explanation in paper
for num_item in [50]:
    for k in [10]:
        print(f"====Num item: {num_item}, cut-off: {k}===")
        test_max_min_IFD_mul(num_item,cut_off=k, pos_item=pos_item, dataframe=True)

# II-F and AI-F

In [ ]:
import numpy as np
def compute_IIF_AIF(m, num_items, rec, rel, gamma=0.8):
    #build user-item matrix
    user_item_rel = np.zeros((m, num_items))

    rank_matrix = np.zeros_like(user_item_rel)
    for i in range(len(rec)):
        rank_matrix[i][rec[i]-1] = np.where(rec[i])[0]+1

    user_item_exp_rbp = np.copy(rank_matrix)

    user_item_exp_rbp[user_item_exp_rbp.nonzero()] = gamma**(user_item_exp_rbp[user_item_exp_rbp.nonzero()]-1)

    for u in range(len(rel)):
        for i in rel[u]:
            user_item_rel[u][i-1] = 1

    #start II-F and AI-F
    r_u_star = user_item_rel.sum(1)[:,np.newaxis]

    e_ui_star = user_item_rel  * (1-np.power(gamma, r_u_star))/(1-gamma)
    r_u_star[r_u_star==0] = 1

    e_ui_star /= r_u_star

    diff = user_item_exp_rbp - e_ui_star
    II_F = np.power(diff, 2).mean()
    AI_F = np.power(diff.mean(0),2).mean()

    return II_F, AI_F

## Limitation 1 (non-real)

In [ ]:
def simulate_IIF_AIF(k, num_items, num_user):
    df = pd.DataFrame()

    item_matrix_u_pool = itertools.permutations(range(num_items),r=k)
    item_matrix_pool = itertools.combinations_with_replacement(item_matrix_u_pool, r=num_user)
    item_matrix_pool = list(item_matrix_pool)


    pos_item_matrix_pool = []
    for i in range(1,num_items+1):
        pos_item_matrix_u_pool = itertools.permutations(range(num_items),r=i)
        pos_item_matrix_pool.extend(list(pos_item_matrix_u_pool))
    pos_item_matrix_pool = itertools.product(pos_item_matrix_pool, repeat=num_user)
    pos_item_matrix_pool = list(pos_item_matrix_pool)

    for item_matrix in item_matrix_pool:
        item_matrix = np.asarray(item_matrix) + 1 #index starts from 1


        for pos_items in pos_item_matrix_pool:
            try:
                pos_items = np.asarray(pos_items, dtype="int") + 1 #index starts from 1
            except:
                pos_items = np.asarray(pos_items, dtype="object")
                for pos_item_u in pos_items:
                    pos_item_u = np.asarray(pos_item_u, dtype=int) + 1 #index starts from 1
            rel_top_k = [np.in1d(u, pos_items_u) for u, pos_items_u in zip(item_matrix, pos_items)]
            rel_top_k = np.asarray(rel_top_k).astype(int)

            new = {'item_matrix': [str(item_matrix.tolist())], 'rel_top_k': [str(rel_top_k.tolist())], 'pos_items': [str(pos_items.tolist())], 'score': [compute_IIF_AIF(num_user, num_items, item_matrix, pos_items)]}
            new = pd.DataFrame(new)
            df = pd.concat([df,new], ignore_index=True)
    return df

In [ ]:
df = simulate_IIF_AIF(2,3,2)

[[1, 2], [1, 2]] [[1, 0], [1, 0]] [[1], [1]] (0.21333333333333337, 0.21333333333333337)
[[1, 2], [1, 2]] [[1, 0], [0, 1]] [[1], [2]] (0.28, 0.11333333333333334)
[[1, 2], [1, 2]] [[1, 0], [0, 0]] [[1], [3]] (0.5466666666666667, 0.38000000000000006)
[[1, 2], [1, 2]] [[0, 0], [1, 0]] [(0,), (0, 1)] (0.6833333333333335, 0.6150000000000001)
[[1, 2], [1, 2]] [[0, 0], [0, 1]] [(0,), (0, 2)] (0.7433333333333333, 0.6749999999999999)
[[1, 2], [1, 2]] [[0, 0], [1, 0]] [(0,), (1, 0)] (0.6833333333333335, 0.6150000000000001)
[[1, 2], [1, 2]] [[0, 0], [1, 1]] [(0,), (1, 2)] (0.44333333333333336, 0.225)
[[1, 2], [1, 2]] [[0, 0], [0, 1]] [(0,), (2, 0)] (0.7433333333333333, 0.6749999999999999)
[[1, 2], [1, 2]] [[0, 0], [1, 1]] [(0,), (2, 1)] (0.44333333333333336, 0.225)
[[1, 2], [1, 2]] [[0, 0], [1, 1]] [(0,), (0, 1, 2)] (0.556088888888889, 0.4429333333333334)
[[1, 2], [1, 2]] [[0, 0], [1, 1]] [(0,), (0, 2, 1)] (0.556088888888889, 0.4429333333333334)
[[1, 2], [1, 2]] [[0, 0], [1, 1]] [(0,), (1, 0, 2)] 

In [ ]:
df[["IIF", "AIF"]] = df.score.apply(pd.Series)

In [ ]:
df[df.IIF == df.IIF.min()]

item_matrix         rel_top_k         pos_items  \
48    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[1, 2], [1, 2]]   
50    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[1, 2], [2, 1]]   
78    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[2, 1], [1, 2]]   
80    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[2, 1], [2, 1]]   
274   [[1, 2], [1, 3]]  [[1, 1], [1, 1]]  [[1, 2], [1, 3]]   
...                ...               ...               ...   
4388  [[3, 1], [3, 2]]  [[1, 1], [1, 1]]  [[3, 1], [3, 2]]   
4596  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [2, 3]]   
4598  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [3, 2]]   
4626  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [2, 3]]   
4628  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [3, 2]]   

                                             score       IIF       AIF  
48    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
50    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
78    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
80    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
274   (0.006666666666666664, 0.005000000000000002)  0.006667  0.005000  
...                                            ...       ...       ...  
4388  (0.006666666666666664, 0.005000000000000002)  0.006667  0.005000  
4596  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4598  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4626  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4628  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  

[84 rows x 6 columns]

In [ ]:
df[df.IIF == df.IIF.min()].rel_top_k.unique()

array(['[[1, 1], [1, 1]]'], dtype=object)

In [ ]:
df[df.IIF == df.IIF.min()]

item_matrix         rel_top_k         pos_items  \
48    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[1, 2], [1, 2]]   
50    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[1, 2], [2, 1]]   
78    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[2, 1], [1, 2]]   
80    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[2, 1], [2, 1]]   
274   [[1, 2], [1, 3]]  [[1, 1], [1, 1]]  [[1, 2], [1, 3]]   
...                ...               ...               ...   
4388  [[3, 1], [3, 2]]  [[1, 1], [1, 1]]  [[3, 1], [3, 2]]   
4596  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [2, 3]]   
4598  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [3, 2]]   
4626  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [2, 3]]   
4628  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [3, 2]]   

                                             score       IIF       AIF  
48    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
50    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
78    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
80    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
274   (0.006666666666666664, 0.005000000000000002)  0.006667  0.005000  
...                                            ...       ...       ...  
4388  (0.006666666666666664, 0.005000000000000002)  0.006667  0.005000  
4596  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4598  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4626  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4628  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  

[84 rows x 6 columns]

In [ ]:
df[df.IIF == df.IIF.max()].rel_top_k.unique()

array(['[[0, 0], [0, 0]]'], dtype=object)

In [ ]:
df[df.IIF == df.IIF.min()]

item_matrix         rel_top_k         pos_items  \
48    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[1, 2], [1, 2]]   
50    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[1, 2], [2, 1]]   
78    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[2, 1], [1, 2]]   
80    [[1, 2], [1, 2]]  [[1, 1], [1, 1]]  [[2, 1], [2, 1]]   
274   [[1, 2], [1, 3]]  [[1, 1], [1, 1]]  [[1, 2], [1, 3]]   
...                ...               ...               ...   
4388  [[3, 1], [3, 2]]  [[1, 1], [1, 1]]  [[3, 1], [3, 2]]   
4596  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [2, 3]]   
4598  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [3, 2]]   
4626  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [2, 3]]   
4628  [[3, 2], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [3, 2]]   

                                             score       IIF       AIF  
48    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
50    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
78    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
80    (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
274   (0.006666666666666664, 0.005000000000000002)  0.006667  0.005000  
...                                            ...       ...       ...  
4388  (0.006666666666666664, 0.005000000000000002)  0.006667  0.005000  
4596  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4598  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4626  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  
4628  (0.006666666666666664, 0.006666666666666664)  0.006667  0.006667  

[84 rows x 6 columns]

In [ ]:
df[df.IIF == df.IIF.min()].rel_top_k.unique()

array(['[[1, 1], [1, 1]]'], dtype=object)

In [ ]:
df[df.IIF == df.IIF.max()]

item_matrix         rel_top_k   pos_items  \
256   [[1, 2], [1, 3]]  [[0, 0], [0, 0]]  [[3], [2]]   
705   [[1, 2], [2, 3]]  [[0, 0], [0, 0]]  [[3], [1]]   
1366  [[1, 3], [1, 3]]  [[0, 0], [0, 0]]  [[2], [2]]   
1815  [[1, 3], [2, 3]]  [[0, 0], [0, 0]]  [[2], [1]]   
2730  [[2, 1], [2, 3]]  [[0, 0], [0, 0]]  [[3], [1]]   
3375  [[2, 3], [2, 3]]  [[0, 0], [0, 0]]  [[1], [1]]   

                                          score   IIF       AIF  
256                  (0.8800000000000002, 0.34)  0.88  0.340000  
705    (0.8800000000000002, 0.2733333333333334)  0.88  0.273333  
1366                 (0.8800000000000002, 0.88)  0.88  0.880000  
1815  (0.8800000000000002, 0.21333333333333337)  0.88  0.213333  
2730                 (0.8800000000000002, 0.34)  0.88  0.340000  
3375                 (0.8800000000000002, 0.88)  0.88  0.880000

In [ ]:
df[df.IIF == df.IIF.max()].rel_top_k.unique()

array(['[[0, 0], [0, 0]]'], dtype=object)

In [ ]:
df[df.AIF == df.AIF.min()]


item_matrix         rel_top_k         pos_items  \
498   [[1, 2], [2, 1]]  [[1, 1], [1, 1]]  [[1, 2], [1, 2]]   
500   [[1, 2], [2, 1]]  [[1, 1], [1, 1]]  [[1, 2], [2, 1]]   
528   [[1, 2], [2, 1]]  [[1, 1], [1, 1]]  [[2, 1], [1, 2]]   
530   [[1, 2], [2, 1]]  [[1, 1], [1, 1]]  [[2, 1], [2, 1]]   
2089  [[1, 3], [3, 1]]  [[1, 1], [1, 1]]  [[1, 3], [1, 3]]   
2092  [[1, 3], [3, 1]]  [[1, 1], [1, 1]]  [[1, 3], [3, 1]]   
2134  [[1, 3], [3, 1]]  [[1, 1], [1, 1]]  [[3, 1], [1, 3]]   
2137  [[1, 3], [3, 1]]  [[1, 1], [1, 1]]  [[3, 1], [3, 1]]   
3921  [[2, 3], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [2, 3]]   
3923  [[2, 3], [3, 2]]  [[1, 1], [1, 1]]  [[2, 3], [3, 2]]   
3951  [[2, 3], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [2, 3]]   
3953  [[2, 3], [3, 2]]  [[1, 1], [1, 1]]  [[3, 2], [3, 2]]   

                                              score       IIF           AIF  
498   (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
500   (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
528   (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
530   (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
2089  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
2092  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
2134  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
2137  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
3921  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
3923  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
3951  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33  
3953  (0.006666666666666664, 8.217301096052206e-33)  0.006667  8.217301e-33

In [ ]:
df[df.AIF == df.AIF.min()].rel_top_k.unique()

array(['[[1, 1], [1, 1]]'], dtype=object)

In [ ]:
df[df.AIF == df.AIF.max()]

item_matrix         rel_top_k   pos_items  \
32    [[1, 2], [1, 2]]  [[0, 0], [0, 0]]  [[3], [3]]   
1366  [[1, 3], [1, 3]]  [[0, 0], [0, 0]]  [[2], [2]]   
2507  [[2, 1], [2, 1]]  [[0, 0], [0, 0]]  [[3], [3]]   
3375  [[2, 3], [2, 3]]  [[0, 0], [0, 0]]  [[1], [1]]   
4066  [[3, 1], [3, 1]]  [[0, 0], [0, 0]]  [[2], [2]]   
4500  [[3, 2], [3, 2]]  [[0, 0], [0, 0]]  [[1], [1]]   

                           score   IIF   AIF  
32                  (0.88, 0.88)  0.88  0.88  
1366  (0.8800000000000002, 0.88)  0.88  0.88  
2507                (0.88, 0.88)  0.88  0.88  
3375  (0.8800000000000002, 0.88)  0.88  0.88  
4066                (0.88, 0.88)  0.88  0.88  
4500                (0.88, 0.88)  0.88  0.88

In [ ]:
df[df.AIF == df.AIF.max()].rel_top_k.unique()

array(['[[0, 0], [0, 0]]'], dtype=object)

Maybe smarter way:

In [ ]:
import numpy as np

In [ ]:
df_iif = pd.DataFrame()

# setting: k=2, m=2, n=3
list_exp = [1, 0.8, 0]
exp_per_round = itertools.permutations(list_exp, 3)
list_exp_two_rounds = list(exp_per_round)
combin_list_exp_two_rounds = itertools.combinations_with_replacement(list_exp_two_rounds, 2)
combin_list_exp_two_rounds = list(combin_list_exp_two_rounds)

avg_across_rounds = [np.asarray(x).mean(0) for x in combin_list_exp_two_rounds]
combin_list_exp_two_rounds_two_users = itertools.combinations_with_replacement(avg_across_rounds, 2)
combin_list_exp_two_rounds_two_users = list(combin_list_exp_two_rounds_two_users)

#enumerate all possible list of Eui star, given 1, 2, or 3 relevant items per user
list_rel = [[1,0,0],[0,1,0], [0,0,1], [0.9,0.9,0],[0.9,0,0.9],[0,0.9,0.9],[0.813,0.813,0.813]]
rel_two_user = list(itertools.combinations_with_replacement(list_rel, 2))

for exp in combin_list_exp_two_rounds_two_users:
    eui = np.asarray(exp).reshape(2,3)
    for rel in rel_two_user:
        rel = np.asarray(rel).reshape(2,3)
        iif = np.power(rel-eui,2).mean()
        print(eui.tolist(), rel.tolist(), iif)
        new = {'eui': [str(eui.tolist())], 'eui_star': [str(rel.tolist())], 'score': [iif]}
        new = pd.DataFrame(new)
        df_iif = pd.concat([df_iif, new])

Streaming output truncated to the last 5000 lines.
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.0, 1.0, 0.0], [0.813, 0.813, 0.813]] 0.19935116666666666
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0, 0, 1], [0, 0, 1]] 0.6900000000000001
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.0, 0.0, 1.0], [0.9, 0.9, 0.0]] 0.5066666666666667
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.0, 0.0, 1.0], [0.9, 0.0, 0.9]] 0.6866666666666666
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.0, 0.0, 1.0], [0.0, 0.9, 0.9]] 0.5066666666666667
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.0, 0.0, 1.0], [0.813, 0.813, 0.813]] 0.4993511666666666
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.9, 0.9, 0.0], [0.9, 0.9, 0.0]] 0.07
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.9, 0.9, 0.0], [0.9, 0.0, 0.9]] 0.25
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.9, 0.9, 0.0], [0.0, 0.9, 0.9]] 0.07
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.9, 0.9, 0.0], [0.813, 0.813, 0.813]] 0.06268449999999999
[[0.9, 0.9, 0.0], [0.4, 1.0, 0.4]] [[0.9, 0.0, 0.9], [0.9, 0.0, 0.9]] 0.52
[[0.9, 0.9, 0.0], 

In [ ]:
df_iif.score.min()

0.0

In [ ]:
df_iif.score.max()

0.8800000000000002

With 3 rounds

In [ ]:
df_iif = pd.DataFrame()
# setting: k=2, m=2, n=3
list_exp = [1, 0.8, 0]
exp_per_round = itertools.permutations(list_exp, 3)
list_exp_3_rounds = list(exp_per_round)
combin_list_exp_3_rounds = itertools.combinations_with_replacement(list_exp_3_rounds, 3)
combin_list_exp_3_rounds = list(combin_list_exp_3_rounds)

avg_across_rounds = [np.asarray(x).mean(0) for x in combin_list_exp_3_rounds]
combin_list_exp_3_rounds_two_users = itertools.combinations_with_replacement(avg_across_rounds, 2)
combin_list_exp_3_rounds_two_users = list(combin_list_exp_3_rounds_two_users)

#enumerate all possible list of Eui star, given 1, 2, or 3 relevant items per user
list_rel = [[1,0,0],[0,1,0], [0,0,1], [0.9,0.9,0],[0.9,0,0.9],[0,0.9,0.9],[0.813,0.813,0.813]]
rel_two_user = list(itertools.combinations_with_replacement(list_rel, 2))

for exp in combin_list_exp_3_rounds_two_users:
    eui = np.asarray(exp).reshape(2,3)
    for rel in rel_two_user:
        rel = np.asarray(rel).reshape(2,3)
        iif = np.power(rel-eui,2).mean()
        print(eui.tolist(), rel.tolist(), iif)
        new = {'eui': [str(eui.tolist())], 'eui_star': [str(rel.tolist())], 'score': [iif]}
        new = pd.DataFrame(new)
        df_iif = pd.concat([df_iif, new])

Streaming output truncated to the last 5000 lines.
[[0.8000000000000002, 0.6666666666666666, 0.3333333333333333], [0.5333333333333333, 0.26666666666666666, 1.0]] [[0.0, 1.0, 0.0], [0.813, 0.813, 0.813]] 0.21231412962962967
[[0.8000000000000002, 0.6666666666666666, 0.3333333333333333], [0.5333333333333333, 0.26666666666666666, 1.0]] [[0, 0, 1], [0, 0, 1]] 0.31407407407407417
[[0.8000000000000002, 0.6666666666666666, 0.3333333333333333], [0.5333333333333333, 0.26666666666666666, 1.0]] [[0.0, 0.0, 1.0], [0.9, 0.9, 0.0]] 0.5107407407407408
[[0.8000000000000002, 0.6666666666666666, 0.3333333333333333], [0.5333333333333333, 0.26666666666666666, 1.0]] [[0.0, 0.0, 1.0], [0.9, 0.0, 0.9]] 0.29074074074074086
[[0.8000000000000002, 0.6666666666666666, 0.3333333333333333], [0.5333333333333333, 0.26666666666666666, 1.0]] [[0.0, 0.0, 1.0], [0.0, 0.9, 0.9]] 0.3707407407407408
[[0.8000000000000002, 0.6666666666666666, 0.3333333333333333], [0.5333333333333333, 0.26666666666666666, 1.0]] [[0.0, 0.0, 1.0]

In [ ]:
df_iif

eui  \
0   [[1.0, 0.8000000000000002, 0.0], [1.0, 0.80000...   
0   [[1.0, 0.8000000000000002, 0.0], [1.0, 0.80000...   
0   [[1.0, 0.8000000000000002, 0.0], [1.0, 0.80000...   
0   [[1.0, 0.8000000000000002, 0.0], [1.0, 0.80000...   
0   [[1.0, 0.8000000000000002, 0.0], [1.0, 0.80000...   
..                                                ...   
0   [[0.0, 0.8000000000000002, 1.0], [0.0, 0.80000...   
0   [[0.0, 0.8000000000000002, 1.0], [0.0, 0.80000...   
0   [[0.0, 0.8000000000000002, 1.0], [0.0, 0.80000...   
0   [[0.0, 0.8000000000000002, 1.0], [0.0, 0.80000...   
0   [[0.0, 0.8000000000000002, 1.0], [0.0, 0.80000...   

                                          eui_star     score  
0                           [[1, 0, 0], [1, 0, 0]]  0.213333  
0                           [[1, 0, 0], [0, 1, 0]]  0.280000  
0                           [[1, 0, 0], [0, 0, 1]]  0.546667  
0               [[1.0, 0.0, 0.0], [0.9, 0.9, 0.0]]  0.110000  
0               [[1.0, 0.0, 0.0], [0.9, 0.0, 0.9]]  0.350000  
..                                             ...       ...  
0               [[0.9, 0.0, 0.9], [0.0, 0.9, 0.9]]  0.246667  
0         [[0.9, 0.0, 0.9], [0.813, 0.813, 0.813]]  0.359351  
0               [[0.0, 0.9, 0.9], [0.0, 0.9, 0.9]]  0.006667  
0         [[0.0, 0.9, 0.9], [0.813, 0.813, 0.813]]  0.119351  
0   [[0.813, 0.813, 0.813], [0.813, 0.813, 0.813]]  0.232036  

[44688 rows x 3 columns]

In [ ]:
df_iif.score.min() # to check

0.000740740740740738

In [ ]:
df_iif[df_iif.score==df_iif.score.min()]

eui  \
0  [[0.9333333333333332, 0.8666666666666667, 0.0]...   
0  [[0.9333333333333332, 0.8666666666666667, 0.0]...   
0  [[0.9333333333333332, 0.8666666666666667, 0.0]...   
0  [[0.9333333333333332, 0.8666666666666667, 0.0]...   
0  [[0.9333333333333332, 0.8666666666666667, 0.0]...   
0  [[0.9333333333333332, 0.8666666666666667, 0.0]...   
0  [[0.8666666666666667, 0.9333333333333332, 0.0]...   
0  [[0.8666666666666667, 0.9333333333333332, 0.0]...   
0  [[0.8666666666666667, 0.9333333333333332, 0.0]...   
0  [[0.8666666666666667, 0.9333333333333332, 0.0]...   
0  [[0.8666666666666667, 0.9333333333333332, 0.0]...   
0  [[0.9333333333333332, 0.0, 0.8666666666666667]...   
0  [[0.9333333333333332, 0.0, 0.8666666666666667]...   
0  [[0.9333333333333332, 0.0, 0.8666666666666667]...   
0  [[0.9333333333333332, 0.0, 0.8666666666666667]...   
0  [[0.8666666666666667, 0.0, 0.9333333333333332]...   
0  [[0.8666666666666667, 0.0, 0.9333333333333332]...   
0  [[0.8666666666666667, 0.0, 0.9333333333333332]...   
0  [[0.0, 0.9333333333333332, 0.8666666666666667]...   
0  [[0.0, 0.9333333333333332, 0.8666666666666667]...   
0  [[0.0, 0.8666666666666667, 0.9333333333333332]...   

                             eui_star     score  
0  [[0.9, 0.9, 0.0], [0.9, 0.9, 0.0]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.9, 0.9, 0.0]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.9, 0.0, 0.9]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.9, 0.0, 0.9]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.9, 0.9, 0.0]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.9, 0.0, 0.9]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.9, 0.0, 0.9]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.9, 0.9, 0.0], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.9, 0.0, 0.9], [0.9, 0.0, 0.9]]  0.000741  
0  [[0.9, 0.0, 0.9], [0.9, 0.0, 0.9]]  0.000741  
0  [[0.9, 0.0, 0.9], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.9, 0.0, 0.9], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.9, 0.0, 0.9], [0.9, 0.0, 0.9]]  0.000741  
0  [[0.9, 0.0, 0.9], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.9, 0.0, 0.9], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.0, 0.9, 0.9], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.0, 0.9, 0.9], [0.0, 0.9, 0.9]]  0.000741  
0  [[0.0, 0.9, 0.9], [0.0, 0.9, 0.9]]  0.000741

In [ ]:
df_iif.score.max() # to check

0.8800000000000002

## Resolving non-realisability

In [ ]:
from sympy.utilities.iterables import multiset_permutations

In [ ]:
#smarter simulation

#num user = 1
def smart_simulate_IIF_AIF(k: int,n: int, num_rel: int, gamma=0.8):
    assert num_rel <= n
    assert k <= n

    df_iif = pd.DataFrame()

    pos_index = np.arange(n)
    rbp_weight =  gamma ** pos_index
    rbp_weight[k:] = 0
    #here we fix the weight to be monotonically decreasing, and only vary the position of the relevant items
    #this won't work for AI-F, since it requires item-level aggregation

    #enumerate all possible list of Eui star, given x relevant items per user
    num_irrel = n - num_rel

    #this e_ui is e_ui_star, eui = e_ui
    e_ui = (1-gamma**num_rel)
    e_ui /= (1-gamma)
    e_ui /= num_rel

    list_rel = num_rel*[e_ui]+num_irrel*[0]
    rel_user = list(multiset_permutations(list_rel))

    eui = rbp_weight
    for rel in rel_user:
        rel = np.asarray(rel).reshape(1,n)
        iif = np.power(rel-eui,2).mean()
        rel[rel.nonzero()] = 1 # for easier inspection
        rel = rel.astype(int)
        new = {'rel': [tuple(rel.tolist()[0])], 'IIF': [iif]}
        new = pd.DataFrame(new)
        df_iif = pd.concat([df_iif, new], ignore_index=True)

    min_iif = df_iif.IIF.min()
    max_iif = df_iif.IIF.max()

    # converting to tuple as the querying doesn't work if it's list...
    list_min = tuple(num_rel*[1]+num_irrel*[0]) #place all relevant items at the top
    list_max = tuple(num_irrel*[0]+num_rel*[1]) #place all relevant items at the bottom

    temp_df = df_iif.query("rel==@list_min | rel==@list_max")
    unique_score = temp_df.IIF.unique()
    min_guess = unique_score.min()
    max_guess = unique_score.max()

    tol = 0.0001
    try:
        assert min_iif in unique_score
    except:
        min_diff = abs(min_iif-min_guess)
        if min_diff > tol:
            print(f"Assertion fails for min II-F, score difference is {min_diff}")
            temp_df = df_iif.query("IIF==@min_iif| rel==@list_min")
            display(temp_df)
    try:
        assert max_iif in unique_score
    except:
        max_diff = abs(max_iif-max_guess)
        if max_diff > tol:
            print(f"Assertion fails for max II-F, score difference is {max_diff}")
            temp_df = df_iif.query("IIF==@max_iif | rel==@list_max")
            display(temp_df)

In [ ]:
for k in [1, 3, 5, 10]:
    for n in [10, 15, 20]:
        for num_rel in range(1,n):
            print(f"====Num item: {n}, cut-off: {k}, num of relevant items: {num_rel}===")
            smart_simulate_IIF_AIF(k,n,num_rel)

====Num item: 10, cut-off: 1, num of relevant items: 1===
====Num item: 10, cut-off: 1, num of relevant items: 2===
====Num item: 10, cut-off: 1, num of relevant items: 3===
====Num item: 10, cut-off: 1, num of relevant items: 4===
====Num item: 10, cut-off: 1, num of relevant items: 5===
====Num item: 10, cut-off: 1, num of relevant items: 6===
====Num item: 10, cut-off: 1, num of relevant items: 7===
====Num item: 10, cut-off: 1, num of relevant items: 8===
====Num item: 10, cut-off: 1, num of relevant items: 9===
====Num item: 15, cut-off: 1, num of relevant items: 1===
====Num item: 15, cut-off: 1, num of relevant items: 2===
====Num item: 15, cut-off: 1, num of relevant items: 3===
====Num item: 15, cut-off: 1, num of relevant items: 4===
====Num item: 15, cut-off: 1, num of relevant items: 5===
====Num item: 15, cut-off: 1, num of relevant items: 6===
====Num item: 15, cut-off: 1, num of relevant items: 7===
====Num item: 15, cut-off: 1, num of relevant items: 8===
====Num item: 

## Limitation 2

But didn't include this example in the writing for brevity

In [ ]:
import numpy as np

In [ ]:
e_ui = np.array([[1,0.8,0,0,0]])
e_ui_star = np.array([[0.67232]*5])

diff = e_ui - e_ui_star
II_F = np.power(diff, 2).mean()
II_F

0.2959437824

In [ ]:
AI_F = np.power(diff.mean(0),2).mean()
AI_F

0.2959437824

In [ ]:
e_ui = np.array([[1,0.8,0,0,0]])
e_ui_star = np.array([[0.81333,0.81333,0.81333,0,0]])

diff = e_ui - e_ui_star
II_F = np.power(diff, 2).mean()
II_F

0.13930581333999997

In [ ]:
AI_F = np.power(diff.mean(0),2).mean()
AI_F

0.13930581333999997

# HD (Limitation 1)

In [ ]:
from scipy.sparse import csr_matrix
import numpy as np
import itertools

def get_HD(item_matrix, num_items, pos_items, rel_top_k, k):

    '''
    For consistency with the original measure, major parts of this code are taken and
    modified from https://github.com/olivierjeunen/EARS-recsys-2021/blob/main/src/environment.py
    Credits to the original author for the code
    '''

    #initialize
    gamma = 0.9

    rec = item_matrix
    rel_items = pos_items
    m = rec.shape[0]

    r_ui = np.zeros((m, num_items))
    for u in range(len(rel_items)): #this is actually iterating over users, not items
        for i in rel_items[u]:
            r_ui[u][i-1] = 1

    #get optimal recos
    padded_gt = np.argsort(-r_ui, axis=1, kind="stable") + 1 #+1 tocorrect index; np.argsort is by default quicksort, not stable sort
    padded_gt_until_k = padded_gt[:,:k]

    #Q (Relevance) Part; in the original code, Q is R
    #r_ui_prime = normalized_P_R, contains normalised true relevance
    r_ui_prime = r_ui / r_ui.sum(axis=1, keepdims=True)
    r_ui_prime_extend = np.append(np.full((r_ui_prime.shape[0],1),np.inf), r_ui_prime, axis=1) #first col is dummy

    Q = np.take_along_axis(r_ui_prime_extend, padded_gt_until_k, axis=1)
    Q = Q.mean(axis=0)

    #C (Click) Part
    #Exposure term
    one_minus_rel = 1 - rel_top_k
    s_up = np.cumprod(one_minus_rel, axis=-1)[:,:-1]

    #first column needs to be ones
    s_up = np.hstack((np.ones(m).reshape(-1,1), s_up))

    gamma_e_rbp = np.cumprod(gamma*np.ones_like(s_up[0,:]))
    exposure_term = gamma_e_rbp * s_up

    #top k recommended items
    c_up = rel_top_k * exposure_term

    #user-wise normalization
    c_up_prime = c_up / c_up.sum(axis=1, keepdims=True)
    np.nan_to_num(c_up_prime, copy=False) #important because there might be division by 0, convert nans to 0

    indptr = np.arange(m + 1) * rec.shape[1]
    indices = rec.flatten()
    data = c_up_prime.flatten()
    c_ui_full = csr_matrix((data, indices, indptr), shape = (m, num_items+1))

    c_up_gt = np.take_along_axis(c_ui_full, padded_gt_until_k, axis=1)
    c_up_gt /= c_up_gt.sum(axis=1)
    np.nan_to_num(c_up_gt, copy=False)

    C = c_up_gt.mean(axis=0).A1

    #Hellinger Distance between Q and C
    #same result as original code, but slightly faster
    squared_diff = (np.sqrt(Q) - np.sqrt(C))**2
    HD = np.sqrt(1/2) * np.sqrt(squared_diff.sum())

    return HD

In [ ]:
k=5
item_matrix = np.array([[1,2,3,4,5],[6,7,8,9,10]])
pos_items = np.asarray([[1,2,3,4,5],[6,7,8,9,10]])
rel_top_k = np.array([[1,1,1,1,1],[1,1,1,1,1]])
num_items = 10000

get_HD(item_matrix, num_items, pos_items, rel_top_k, k)

0.743496068920369

In [ ]:
import pandas as pd

In [ ]:
def simulate_HD(k, num_items, num_user):
    df = pd.DataFrame()


    item_matrix_u_pool = itertools.combinations_with_replacement(range(num_items),r=k)
    item_matrix_pool = itertools.product(item_matrix_u_pool, repeat=num_user)
    item_matrix_pool = list(item_matrix_pool)


    pos_item_matrix_pool = []
    for i in range(1,num_items+1):
        pos_item_matrix_u_pool = itertools.permutations(range(num_items),r=i)
        pos_item_matrix_pool.extend(list(pos_item_matrix_u_pool))
    pos_item_matrix_pool = itertools.product(pos_item_matrix_pool, repeat=num_user)
    pos_item_matrix_pool = list(pos_item_matrix_pool)

    for item_matrix in item_matrix_pool:
        item_matrix = np.asarray(item_matrix) + 1 #index starts from 1

        for pos_items in pos_item_matrix_pool:
            try:
                pos_items = np.asarray(pos_items, dtype="int") + 1 #index starts from 1
            except:
                pos_items = np.asarray(pos_items, dtype="object")
                for pos_item_u in pos_items:
                    pos_item_u = np.asarray(pos_item_u, dtype=int) + 1 #index starts from 1
            rel_top_k = [np.in1d(u, pos_items_u) for u, pos_items_u in zip(item_matrix, pos_items)]
            rel_top_k = np.asarray(rel_top_k).astype(int)


            print(item_matrix.tolist(), rel_top_k.tolist(), pos_items.tolist(), get_HD(item_matrix, num_items, pos_items, rel_top_k, k))
            new = {'item_matrix': [str(item_matrix.tolist())], 'rel_top_k': [str(rel_top_k.tolist())], 'pos_items': [str(pos_items.tolist())], 'HD': [get_HD(item_matrix, num_items, pos_items, rel_top_k,k)]}
            new = pd.DataFrame(new)
            df = pd.concat([df,new], ignore_index=True)
    return df


In [ ]:
df = simulate_HD(2,3,2)

[[1, 1], [1, 1]] [[1, 1], [1, 1]] [[1], [1]] 0.0
[[1, 1], [1, 1]] [[1, 1], [0, 0]] [[1], [2]] 0.20710678118654752
[[1, 1], [1, 1]] [[1, 1], [0, 0]] [[1], [3]] 0.20710678118654752
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (0, 1)] 0.37098189215136296
[[1, 1], [1, 1]] [[0, 0], [0, 0]] [(0,), (0, 2)] 0.7071067811865475
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (1, 0)] 0.37098189215136296
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (1, 2)] 0.37098189215136296
[[1, 1], [1, 1]] [[0, 0], [0, 0]] [(0,), (2, 0)] 0.7071067811865475
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (2, 1)] 0.37098189215136296
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (0, 1, 2)] 0.2988584907226845
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (0, 2, 1)] 0.2988584907226845
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (1, 0, 2)] 0.2988584907226845
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (1, 2, 0)] 0.2988584907226845
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (2, 0, 1)] 0.2988584907226845
[[1, 1], [1, 1]] [[0, 0], [1, 1]] [(0,), (2, 1, 0)] 0.

<ipython-input-96-d72e6827dc78>:47: RuntimeWarning: invalid value encountered in divide
  c_up_prime = c_up / c_up.sum(axis=1, keepdims=True)
/usr/local/lib/python3.10/dist-packages/scipy/sparse/_base.py:730: RuntimeWarning: divide by zero encountered in divide
  recip = np.true_divide(1., other)


Streaming output truncated to the last 5000 lines.
[[1, 3], [1, 2]] [[1, 1], [1, 1]] [[2, 1, 3], [1, 3, 2]] 0.5059476891376298
[[1, 3], [1, 2]] [[1, 1], [1, 1]] [[2, 1, 3], [2, 1, 3]] 0.5059476891376298
[[1, 3], [1, 2]] [[1, 1], [1, 1]] [[2, 1, 3], [2, 3, 1]] 0.5059476891376298
[[1, 3], [1, 2]] [[1, 1], [1, 1]] [[2, 1, 3], [3, 1, 2]] 0.5059476891376298
[[1, 3], [1, 2]] [[1, 1], [1, 1]] [[2, 1, 3], [3, 2, 1]] 0.5059476891376298
[[1, 3], [1, 2]] [[1, 0], [0, 0]] [(1, 2, 0), (0,)] 0.2988584907226845
[[1, 3], [1, 2]] [[1, 0], [1, 0]] [(1, 2, 0), (1,)] 0.31649658092772603
[[1, 3], [1, 2]] [[1, 0], [0, 1]] [(1, 2, 0), (2,)] 0.31649658092772603
[[1, 3], [1, 2]] [[1, 0], [1, 0]] [(1, 2, 0), (0, 1)] 0.5207393227890168
[[1, 3], [1, 2]] [[1, 0], [0, 1]] [(1, 2, 0), (0, 2)] 0.5207393227890168
[[1, 3], [1, 2]] [[1, 0], [1, 0]] [(1, 2, 0), (1, 0)] 0.5207393227890168
[[1, 3], [1, 2]] [[1, 0], [1, 1]] [(1, 2, 0), (1, 2)] 0.5207393227890168
[[1, 3], [1, 2]] [[1, 0], [0, 1]] [(1, 2, 0), (2, 0)] 0.520739

In [ ]:
df.HD.min()

0.0

In [ ]:
df.HD.max()

0.7071067811865476

In [ ]:
df[df.HD == 0].head(50)

item_matrix         rel_top_k         pos_items   HD
0     [[1, 1], [1, 1]]  [[1, 1], [1, 1]]        [[1], [1]]  0.0
225   [[1, 1], [1, 2]]  [[1, 1], [1, 0]]        [[1], [1]]  0.0
226   [[1, 1], [1, 2]]  [[1, 1], [0, 1]]        [[1], [2]]  0.0
450   [[1, 1], [1, 3]]  [[1, 1], [1, 0]]        [[1], [1]]  0.0
452   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]        [[1], [3]]  0.0
501   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[1, 2], [2, 3]]  0.0
503   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[1, 2], [3, 2]]  0.0
516   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[1, 3], [2, 3]]  0.0
518   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[1, 3], [3, 2]]  0.0
531   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[2, 1], [2, 3]]  0.0
533   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[2, 1], [3, 2]]  0.0
561   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[3, 1], [2, 3]]  0.0
563   [[1, 1], [1, 3]]  [[1, 1], [0, 1]]  [[3, 1], [3, 2]]  0.0
676   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]        [[1], [2]]  0.0
723   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[1, 2], [1, 2]]  0.0
725   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[1, 2], [2, 1]]  0.0
738   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[1, 3], [1, 2]]  0.0
740   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[1, 3], [2, 1]]  0.0
753   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[2, 1], [1, 2]]  0.0
755   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[2, 1], [2, 1]]  0.0
783   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[3, 1], [1, 2]]  0.0
785   [[1, 1], [2, 2]]  [[1, 1], [1, 1]]  [[3, 1], [2, 1]]  0.0
901   [[1, 1], [2, 3]]  [[1, 1], [1, 0]]        [[1], [2]]  0.0
902   [[1, 1], [2, 3]]  [[1, 1], [0, 1]]        [[1], [3]]  0.0
948   [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[1, 2], [1, 2]]  0.0
949   [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[1, 2], [1, 3]]  0.0
950   [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[1, 2], [2, 1]]  0.0
952   [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[1, 2], [3, 1]]  0.0
963   [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[1, 3], [1, 2]]  0.0
964   [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[1, 3], [1, 3]]  0.0
965   [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[1, 3], [2, 1]]  0.0
967   [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[1, 3], [3, 1]]  0.0
978   [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[2, 1], [1, 2]]  0.0
979   [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[2, 1], [1, 3]]  0.0
980   [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[2, 1], [2, 1]]  0.0
982   [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[2, 1], [3, 1]]  0.0
1008  [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[3, 1], [1, 2]]  0.0
1009  [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[3, 1], [1, 3]]  0.0
1010  [[1, 1], [2, 3]]  [[1, 1], [1, 0]]  [[3, 1], [2, 1]]  0.0
1012  [[1, 1], [2, 3]]  [[1, 1], [0, 1]]  [[3, 1], [3, 1]]  0.0
1127  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]        [[1], [3]]  0.0
1174  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 2], [1, 3]]  0.0
1176  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 2], [2, 3]]  0.0
1177  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 2], [3, 1]]  0.0
1178  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 2], [3, 2]]  0.0
1189  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 3], [1, 3]]  0.0
1191  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 3], [2, 3]]  0.0
1192  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 3], [3, 1]]  0.0
1193  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[1, 3], [3, 2]]  0.0
1204  [[1, 1], [3, 3]]  [[1, 1], [1, 1]]  [[2, 1], [1, 3]]  0.0

In [ ]:
df[df.HD == df.HD.max()]

item_matrix         rel_top_k         pos_items        HD
16    [[1, 1], [1, 1]]  [[0, 0], [0, 0]]        [[2], [2]]  0.707107
17    [[1, 1], [1, 1]]  [[0, 0], [0, 0]]        [[2], [3]]  0.707107
31    [[1, 1], [1, 1]]  [[0, 0], [0, 0]]        [[3], [2]]  0.707107
32    [[1, 1], [1, 1]]  [[0, 0], [0, 0]]        [[3], [3]]  0.707107
96    [[1, 1], [1, 1]]  [[0, 0], [0, 0]]  [[2, 3], [2, 3]]  0.707107
...                ...               ...               ...       ...
7891  [[3, 3], [3, 3]]  [[0, 0], [0, 0]]        [[2], [2]]  0.707107
7923  [[3, 3], [3, 3]]  [[0, 0], [0, 0]]  [[1, 2], [1, 2]]  0.707107
7925  [[3, 3], [3, 3]]  [[0, 0], [0, 0]]  [[1, 2], [2, 1]]  0.707107
7953  [[3, 3], [3, 3]]  [[0, 0], [0, 0]]  [[2, 1], [1, 2]]  0.707107
7955  [[3, 3], [3, 3]]  [[0, 0], [0, 0]]  [[2, 1], [2, 1]]  0.707107

[117 rows x 4 columns]

In [ ]:
df[df.HD == df.HD.max()].rel_top_k.unique()

array(['[[0, 0], [0, 0]]'], dtype=object)